# Filip Michalsky - Blockhouse Work Trial


For this Blockhouse Work Trial, we will run our work on Google Collab (easy access to a GPU to train the Transformer model)

We are going to focus on training a transformer and PPO policy on the training market data from scratch (first 70% of the intra-day trades on July 3, 2023 and evaluate on the last 30% of the intra-day trades of the same day).

## Setup Google Collab + Installations

In [1]:
# prompt: please load a file from current dir in google drive - same as notebook

from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [2]:
!ls /content/drive/MyDrive/Job_stuff/Blockhouse_Work_Trial/xnas-itch-20230703.tbbo.csv

/content/drive/MyDrive/Job_stuff/Blockhouse_Work_Trial/xnas-itch-20230703.tbbo.csv


In [3]:
!wget http://prdownloads.sourceforge.net/ta-lib/ta-lib-0.4.0-src.tar.gz
!tar -xzvf ta-lib-0.4.0-src.tar.gz
%cd ta-lib
!./configure --prefix=/usr
!make
!make install
!pip install TA-Lib

--2024-08-09 08:04:54--  http://prdownloads.sourceforge.net/ta-lib/ta-lib-0.4.0-src.tar.gz
Resolving prdownloads.sourceforge.net (prdownloads.sourceforge.net)... 204.68.111.105
Connecting to prdownloads.sourceforge.net (prdownloads.sourceforge.net)|204.68.111.105|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz [following]
--2024-08-09 08:04:54--  http://downloads.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz
Resolving downloads.sourceforge.net (downloads.sourceforge.net)... 204.68.111.105
Reusing existing connection to prdownloads.sourceforge.net:80.
HTTP request sent, awaiting response... 302 Found
Location: http://versaweb.dl.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz?viasf=1 [following]
--2024-08-09 08:04:54--  http://versaweb.dl.sourceforge.net/project/ta-lib/ta-lib/0.4.0/ta-lib-0.4.0-src.tar.gz?viasf=1
Resolvi

In [4]:
!pip install stable_baselines3 shimmy==1.3.0

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

## Load Data

In [5]:
import pandas as pd
import numpy as np
import talib as ta

class TechnicalIndicators:
    def __init__(self, data):
        self.data = data

    def add_momentum_indicators(self):
        self.data['RSI'] = ta.RSI(self.data['Close'], timeperiod=14)
        self.data['MACD'], self.data['MACD_signal'], self.data['MACD_hist'] = ta.MACD(self.data['Close'], fastperiod=12, slowperiod=26, signalperiod=9)
        self.data['Stoch_k'], self.data['Stoch_d'] = ta.STOCH(self.data['High'], self.data['Low'], self.data['Close'],
                                                              fastk_period=14, slowk_period=3, slowd_period=3)

    def add_volume_indicators(self):
        self.data['OBV'] = ta.OBV(self.data['Close'], self.data['Volume'])

    def add_volatility_indicators(self):
        self.data['Upper_BB'], self.data['Middle_BB'], self.data['Lower_BB'] = ta.BBANDS(self.data['Close'], timeperiod=20)
        self.data['ATR_1'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=1)
        self.data['ATR_2'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=2)
        self.data['ATR_5'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=5)
        self.data['ATR_10'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=10)
        self.data['ATR_20'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=20)

    def add_trend_indicators(self):
        self.data['ADX'] = ta.ADX(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['+DI'] = ta.PLUS_DI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['-DI'] = ta.MINUS_DI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['CCI'] = ta.CCI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=5)

    def add_other_indicators(self):
        self.data['DLR'] = np.log(self.data['Close'] / self.data['Close'].shift(1))
        self.data['TWAP'] = self.data['Close'].expanding().mean()
        self.data['VWAP'] = (self.data['Volume'] * (self.data['High'] + self.data['Low']) / 2).cumsum() / self.data['Volume'].cumsum()

    def add_all_indicators(self):
        self.add_momentum_indicators()
        self.add_volume_indicators()
        self.add_volatility_indicators()
        self.add_trend_indicators()
        self.add_other_indicators()
        return self.data

In [6]:
data = pd.read_csv('/content/drive/MyDrive/Job_stuff/Blockhouse_Work_Trial/xnas-itch-20230703.tbbo.csv')


# Preprocessing to create necessary columns
data['price']=data['price']/1e9
data['bid_px_00']=data['bid_px_00']/1e9
data['ask_px_00']=data['ask_px_00']/1e9

data['Close'] = data['price']
data['Volume'] = data['size']
data['High'] = data[['bid_px_00', 'ask_px_00']].max(axis=1)
data['Low'] = data[['bid_px_00', 'ask_px_00']].min(axis=1)
data['Open'] = data['Close'].shift(1).fillna(data['Close'])


ti = TechnicalIndicators(data)
df_with_indicators = ti.add_all_indicators()
market_features_df = df_with_indicators[35:]

In [7]:
# Delete useless features with no signal
useless_features = [
    'rtype', 'publisher_id', 'instrument_id', 'action'
]
# Check which useless features are actually present in the DataFrame
features_to_drop = [feature for feature in useless_features if feature in market_features_df.columns]

# Drop the features if any are present
if features_to_drop:
    market_features_df.drop(columns=features_to_drop, inplace=True)

market_features_df['timestamp']=pd.to_datetime(market_features_df['ts_recv'])

# divide the features df into train and test -> use 60/40 train/test split so we can eval performance for unseen before afternoon trading.
market_features_df.shape
market_features_df.head()

<ipython-input-7-c3b2711fc76c>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  market_features_df.drop(columns=features_to_drop, inplace=True)
<ipython-input-7-c3b2711fc76c>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  market_features_df['timestamp']=pd.to_datetime(market_features_df['ts_recv'])


ts_recv             ts_event side  depth   price  size  flags  \
35  1688371214386057385  1688371214385893078    N      0  194.05    50    130   
36  1688371214386063777  1688371214385899379    N      0  194.05    50    130   
37  1688371215804852019  1688371215804687301    B      0  194.21    10    130   
38  1688371219671476629  1688371219671312224    N      0  194.14    10    130   
39  1688371223368835585  1688371223368671235    B      0  194.13    10    130   

    ts_in_delta  sequence  bid_px_00  ...    ATR_10    ATR_20        ADX  \
35       164307    326232      194.0  ...  0.075141  0.072403  97.257397   
36       164398    326233      194.0  ...  0.097627  0.083783  97.361721   
37       164718    328131      194.0  ...  0.108864  0.090094  97.458593   
38       164405    331406      194.0  ...  0.118978  0.096089  97.548546   
39       164350    334235      194.0  ...  0.121080  0.098285  97.632074   

          +DI       -DI         CCI       DLR        TWAP        VWAP  \
35  30.435801  0.196362  166.666667  0.000000  194.020000  194.021894   
36  22.989295  0.148320   83.333333  0.000000  194.020811  194.025188   
37  19.409454  0.125224   79.268293  0.000824  194.025789  194.025596   
38  16.622008  0.107240   -3.205128 -0.000360  194.028718  194.025873   
39  15.068361  0.097216 -113.095238 -0.000052  194.031250  194.026071   

                       timestamp  
35 2023-07-03 08:00:14.386057385  
36 2023-07-03 08:00:14.386063777  
37 2023-07-03 08:00:15.804852019  
38 2023-07-03 08:00:19.671476629  
39 2023-07-03 08:00:23.368835585  

[5 rows x 44 columns]

In [8]:
# train test split market_features_df

from sklearn.model_selection import train_test_split

train_df, test_df = train_test_split(market_features_df, test_size=0.3, shuffle=False)


In [9]:
# check the end of the day
test_df.tail()

ts_recv             ts_event side  depth   price  size  \
59266  1688417954514485218  1688417954514320323    B      0  192.44     6   
59267  1688417961020718430  1688417961020553920    B      0  192.44     1   
59268  1688417973297905504  1688417973297741235    A      0  192.40     5   
59269  1688417996889779362  1688417996889614660    B      0  192.45     3   
59270  1688417998907430616  1688417998907265922    B      0  192.45     3   

       flags  ts_in_delta   sequence  bid_px_00  ...    ATR_10    ATR_20  \
59266    130       164895  252532002      192.4  ...  0.028636  0.027592   
59267    130       164510  252532102      192.4  ...  0.029772  0.028212   
59268    130       164269  252532347      192.4  ...  0.032795  0.029802   
59269    130       164702  252532944      192.4  ...  0.034515  0.030812   
59270    130       164694  252534572      192.4  ...  0.036064  0.031771   

             ADX       +DI       -DI         CCI       DLR        TWAP  \
59266  15.474528  6.612534  3.765166  118.055556  0.000208  192.701135   
59267  16.329018  5.953254  3.389772   83.333333  0.000000  192.701131   
59268  19.013869  9.751295  2.919558   12.820513 -0.000208  192.701125   
59269  21.506945  8.671762  2.596344  100.000000  0.000260  192.701121   
59270  23.821945  7.748024  2.319775   83.333333  0.000000  192.701117   

             VWAP                     timestamp  
59266  192.722211 2023-07-03 20:59:14.514485218  
59267  192.722211 2023-07-03 20:59:21.020718430  
59268  192.722211 2023-07-03 20:59:33.297905504  
59269  192.722211 2023-07-03 20:59:56.889779362  
59270  192.722211 2023-07-03 20:59:58.907430616  

[5 rows x 44 columns]

## Use Collab's GPU

In [10]:
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [11]:
!nvidia-smi

Fri Aug  9 08:08:30 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA L4                      Off | 00000000:00:03.0 Off |                    0 |
| N/A   31C    P8              11W /  72W |      4MiB / 23034MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

NVIDIA L4
23GB of memory - decent. (no A100s available - sad 😞)

## Trading Environment

In [12]:
import gym
from gym import spaces
import numpy as np
import pandas as pd

class TradingEnvironment(gym.Env):
    metadata = {'render.modes': ['human']}

    def __init__(self, data, daily_trading_limit):
        super(TradingEnvironment, self).__init__()
        self.data = data
        self.daily_trading_limit = daily_trading_limit
        self.current_step = 0
        self.max_steps = len(data) - 1

        # Extract state columns
        self.state_columns = ['Close', 'Volume', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d',
                              'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']

        # Initialize balance, shares held, and total shares traded
        self.balance = 10_000_000.0  # $10 million
        self.shares_held = 0
        self.total_shares_traded = 0

        # Define action space: [Hold, Buy, Sell]
        self.action_space = spaces.Discrete(3)

        # Define observation space based on state columns
        self.observation_space = spaces.Box(
            low=-np.inf, high=np.inf, shape=(len(self.state_columns),), dtype=np.float32
        )

    def reset(self):
        self.current_step = 0
        self.balance = 10_000_000.0  # $10 million
        self.shares_held = 0
        self.total_shares_traded = 0
        self.cumulative_reward = 0
        self.trades = []
        return self._next_observation()

    # def _next_observation(self):
    #     return self.data[self.state_columns].iloc[self.current_step].values
    def _next_observation(self):
        return torch.tensor(self.data[self.state_columns].iloc[self.current_step].values, dtype=torch.float32)


    def step(self, action):
        expected_price = self.data.iloc[self.current_step]['ask_px_00']
        actual_price = self.data.iloc[self.current_step]['price']
        transaction_time = self.data.iloc[self.current_step]['ts_in_delta']
        self._take_action(action)
        reward = 0

        if self.current_step >= len(self.data) - 1:
            self.current_step = 0
        if action != 0:
            transaction_cost= self._calculate_transaction_cost(self.data.iloc[self.current_step]['Volume'], 0.3, self.data['Volume'].mean())
            reward = self._calculate_reward(expected_price, actual_price, transaction_time, transaction_cost)
            self.cumulative_reward += reward
            if self.trades:
                self.trades[-1]['reward'] = reward
                self.trades[-1]['transaction_cost'] = transaction_cost
                self.trades[-1]['slippage'] = expected_price - actual_price
                self.trades[-1]['time_penalty'] = 100*transaction_time/1e9
        done = self.current_step == len(self.data) - 1
        obs = self._next_observation()
        info = {
        'step': self.current_step,
        'action': action,
        'price': actual_price,
        'shares': self.trades[-1]['shares'] if self.trades else 0
    }
        self.current_step += 1

        return obs, reward, done, info

    def _take_action(self, action):
        current_price = self.data.iloc[self.current_step]['Close']
        current_time = pd.to_datetime(self.data.iloc[self.current_step]['ts_event'])
        trade_info = {'step': self.current_step, 'timestamp': current_time, 'action': action, 'price': current_price, 'shares': 0, 'reward': 0, 'transaction_cost': 0, 'slippage': 0, 'time_penalty': 0}

        if action == 1: # and self.total_shares_traded < self.daily_trading_limit:  # Buy
            shares_bought = (self.balance * np.random.uniform(0.001, 0.005)) // current_price
            self.balance -= shares_bought * current_price
            self.shares_held += shares_bought
            self.total_shares_traded += shares_bought
            trade_info['shares'] = shares_bought
            if(shares_bought>0):
                self.trades.append(trade_info)
        elif action == 2: # and self.total_shares_traded < self.daily_trading_limit:  # Sell
            shares_sold = min((self.balance * np.random.uniform(0.001, 0.005)) // current_price, self.shares_held)
            self.balance += shares_sold * current_price
            self.shares_held -= shares_sold
            self.total_shares_traded -= shares_sold
            trade_info['shares'] = shares_sold
            if(shares_sold>0):
                self.trades.append(trade_info)

    def _calculate_reward(self, expected_price, actual_price, transaction_time, transaction_cost):
        slippage = expected_price - actual_price
        time_penalty = 100*transaction_time/1e9
        reward = - (slippage + time_penalty + transaction_cost)
        return reward

    def _calculate_transaction_cost(self, volume, volatility, daily_volume):
        return volatility * np.sqrt(volume / daily_volume)

    def run(self):
        self.reset()
        for _ in range(len(self.data)):
            self.step()
        return self.cumulative_reward, self.trades

    def render(self, mode='human', close=False):
        print(f'Step: {self.current_step}')
        print(f'Balance: {self.balance}')
        print(f'Shares held: {self.shares_held}')
        print(f'Total shares traded: {self.total_shares_traded}')
        print(f'Total portfolio value: {self.balance + self.shares_held * self.data.iloc[self.current_step]["Close"]}')
        print(f'Cumulative reward: {self.cumulative_reward}')
        self.print_trades()

    def print_trades(self):
        # download all trades in a pandas dataframe using .csv
        trades_df = pd.DataFrame(self.trades)
        # Save a csv
        trades_df.to_csv('trades_ppo.csv', index=False)
        for trade in self.trades:
            print(f"Step: {trade['step']}, Timestamp: {trade['timestamp']}, Action: {trade['action']}, Price: {trade['price']}, Shares: {trade['shares']}, Reward: {trade['reward']}, Transaction Cost: {trade['transaction_cost']}, Slippage: {trade['slippage']}, Time Penalty: {trade['time_penalty']}")

## Baseline vanilla transformer model

In [13]:
import torch.nn as nn
import torch.optim as optim
import numpy as np
from typing import List, Dict
import pandas as pd
import psutil
from tqdm import tqdm


def get_memory_usage():
    # CPU Memory
    cpu_memory = psutil.virtual_memory().percent

    # GPU Memory
    if torch.cuda.is_available():
        gpu_memory = torch.cuda.memory_allocated() / torch.cuda.max_memory_allocated() * 100
    else:
        gpu_memory = 0

    return cpu_memory, gpu_memory

def print_with_memory(message):
    cpu_memory, gpu_memory = get_memory_usage()
    print(f"{message} [CPU Memory: {cpu_memory:.2f}%, GPU Memory: {gpu_memory:.2f}%]")


class StatePreprocessor:
    def __init__(self, state_dims: List[str]):
        self.state_dims = state_dims

    def preprocess(self, state: Dict[str, float]) -> torch.Tensor:
        return torch.tensor([state[dim] for dim in self.state_dims], dtype=torch.float32).unsqueeze(0).to(device)

class TransformerTrader(nn.Module):
    def __init__(self, input_dim: int, num_heads: int = 4, num_layers: int = 2, dropout: float = 0.1):
        super().__init__()
        self.input_dim = input_dim
        self.embedding = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.LayerNorm(64)
        )
        self.positional_encoding = nn.Parameter(torch.randn(1, 1, 64))
        encoder_layer = nn.TransformerEncoderLayer(d_model=64, nhead=num_heads, dropout=dropout)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=num_layers)
        self.fc = nn.Linear(64, 3)  # 3 actions: Buy, Sell, Hold
        self.to(device)

    def forward(self, x: torch.Tensor) -> torch.Tensor:

        if x.dim() == 1:
            x = x.unsqueeze(0)  # Add batch dimension if it's missing
        if x.dim() == 2:
            x = x.unsqueeze(1)  # Add sequence dimension if it's missing

        x = x.to(device)

        x = self.embedding(x)
        x = x + self.positional_encoding
        x = self.transformer_encoder(x)
        return self.fc(x.mean(dim=1))


# 4. Training Loop
def train_transformer_trader(env: TradingEnvironment, model: TransformerTrader, num_episodes: int, lr: float = 1e-4, batch_size: int = 32):
    optimizer = optim.Adam(model.parameters(), lr=lr)
    criterion = nn.MSELoss()

    episode_bar = tqdm(range(num_episodes), desc="Episodes")

    for episode in episode_bar:
        state = env.reset()
        episode_reward = 0
        step_count = 0
        portfolio_values = []
        actions_taken = []
        buffer = []

        step_bar = tqdm(total=env.max_steps, desc=f"Episode {episode+1} Steps", leave=False)

        while env.current_step < env.max_steps:
            with torch.no_grad():
                action_probs = model(state)
            action = torch.argmax(action_probs).item()
            next_state, reward, done, info = env.step(action)
            episode_reward += reward

            buffer.append((state, action, reward, next_state, done))
            if len(buffer) >= batch_size:
                batch = list(zip(*buffer))
                states = torch.stack(batch[0])
                actions = torch.tensor(batch[1], dtype=torch.long).to(device)
                rewards = torch.tensor(batch[2], dtype=torch.float32).to(device)
                next_states = torch.stack(batch[3])
                dones = torch.tensor(batch[4], dtype=torch.float32).to(device)

                action_probs = model(states)
                next_action_probs = model(next_states)
                targets = rewards + (0.99 * torch.max(next_action_probs, dim=1)[0] * (1 - dones))
                loss = criterion(action_probs[torch.arange(batch_size), actions], targets)

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                buffer.clear()

            state = next_state
            step_count += 1
            portfolio_values.append(env.balance + env.shares_held * env.data.iloc[env.current_step-1]['Close'])
            actions_taken.append(action)

            step_bar.update(1)
            if step_count % 25 == 0:
                print_with_memory(f"Step: {step_count}, Reward: {episode_reward:.2f}, Portfolio: ${portfolio_values[-1]:.2f}, Action: {['Hold', 'Buy', 'Sell'][action]}, Current Step: {env.current_step}/{env.max_steps}")

        step_bar.close()

        avg_portfolio_value = np.mean(portfolio_values)
        final_portfolio_value = portfolio_values[-1]
        action_distribution = np.bincount(actions_taken, minlength=3) / len(actions_taken)

        print_with_memory(f"Episode {episode+1} completed. Reward: {episode_reward:.2f}, Steps: {step_count}, Avg Portfolio: ${avg_portfolio_value:.2f}, Final Portfolio: ${final_portfolio_value:.2f}, Actions (H/B/S): {action_distribution[0]:.2f}/{action_distribution[1]:.2f}/{action_distribution[2]:.2f}")

    episode_bar.close()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [14]:
# Usage
state_dims = ['Close', 'Volume', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d', 'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']

daily_trading_limit = 1000

# Create the trading environment
env = TradingEnvironment(train_df, daily_trading_limit)

model = TransformerTrader(input_dim=len(state_dims))


/usr/local/lib/python3.10/dist-packages/torch/nn/modules/transformer.py:306: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


In [15]:
train_transformer_trader(env, model, num_episodes=2, batch_size = 64)

Episode 1 Steps:   0%|          | 54/41464 [00:00<05:37, 122.82it/s]

Step: 25, Reward: -1.90, Portfolio: $10000013.34, Action: Hold, Current Step: 25/41464 [CPU Memory: 4.70%, GPU Memory: 91.06%]
Step: 50, Reward: -2.22, Portfolio: $10000028.34, Action: Hold, Current Step: 50/41464 [CPU Memory: 4.70%, GPU Memory: 91.06%]



Episode 1 Steps:   0%|          | 105/41464 [00:02<12:48, 53.81it/s]

Step: 75, Reward: -4.65, Portfolio: $10000028.34, Action: Sell, Current Step: 75/41464 [CPU Memory: 5.40%, GPU Memory: 92.02%]
Step: 100, Reward: -9.13, Portfolio: $10000028.34, Action: Sell, Current Step: 100/41464 [CPU Memory: 5.50%, GPU Memory: 92.02%]



Episode 1 Steps:   0%|          | 159/41464 [00:02<06:39, 103.50it/s]

...

Step: 41350, Reward: -29.31, Portfolio: $10000000.00, Action: Hold, Current Step: 41350/41464 [CPU Memory: 5.40%, GPU Memory: 80.18%]
Step: 41375, Reward: -29.31, Portfolio: $10000000.00, Action: Hold, Current Step: 41375/41464 [CPU Memory: 5.40%, GPU Memory: 80.18%]



Episode 2 Steps: 100%|█████████▉| 41425/41464 [04:00<00:00, 172.98it/s]

Step: 41400, Reward: -29.31, Portfolio: $10000000.00, Action: Hold, Current Step: 41400/41464 [CPU Memory: 5.40%, GPU Memory: 80.18%]
Step: 41425, Reward: -29.31, Portfolio: $10000000.00, Action: Hold, Current Step: 41425/41464 [CPU Memory: 5.40%, GPU Memory: 80.18%]



Episodes: 100%|██████████| 2/2 [07:57<00:00, 238.90s/it]

Step: 41450, Reward: -29.31, Portfolio: $10000000.00, Action: Hold, Current Step: 41450/41464 [CPU Memory: 5.40%, GPU Memory: 80.18%]
Episode 2 completed. Reward: -29.31, Steps: 41464, Avg Portfolio: $10000000.00, Final Portfolio: $10000000.00, Actions (H/B/S): 1.00/0.00/0.00 [CPU Memory: 5.40%, GPU Memory: 80.18%]


### Run the agent in the environment

In [16]:
# calculate performance
observations = []
# Evaluate the model
rewards_list = []
action_probs_list = []
test_env = TradingEnvironment(test_df, daily_trading_limit)
obs = test_env.reset()
for _ in tqdm(range(len(test_df))):
    observations.append(obs)
    # todo - model should learn other features!
    with torch.no_grad():
      action_probs = model(obs)
    action_probs_list.append(action_probs)
    action = torch.argmax(action_probs).item()
    obs, rewards, done, info = test_env.step(action)
    rewards_list.append(rewards)
    if done:
        break


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
100%|██████████| 17771/17771 [01:10<00:00, 252.68it/s]


In [17]:
test_env.render()

Step: 1
Balance: 10000000.0
Shares held: 0
Total shares traded: 0
Total portfolio value: 10000000.0
Cumulative reward: 0


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [18]:
test_env.balance + test_env.shares_held * test_env.data.iloc[test_env.current_step-1]['Close']

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


10000000.0

This vanilla Transformer agent does not do any trades! Improvements would include:
- Feature engineering (create lagging features)
- Change loss function to be cross entropy (since we have 3 categories Hold/Buy/Sell) - I tried this but ran into a lot of numerical instability and exploding gradients in the softmax so came back to optizing MSE - this is not ideal as our task is really classification.

## PPO + Transformer combination

Here we combine a transformer architecture with the proximal policy optimization (PPO).

### Trading env adjustment

In [19]:
## slightly adjusted trading env with easier portfolio calculation

import gym
from gym import spaces
import numpy as np
import pandas as pd
import torch

class TradingEnvironment(gym.Env):
    metadata = {'render.modes': ['human']}

    def __init__(self, data, daily_trading_limit):
        super(TradingEnvironment, self).__init__()
        self.data = data
        self.daily_trading_limit = daily_trading_limit
        self.current_step = 0
        self.max_steps = len(data) - 1

        self.state_columns = ['Close', 'Volume', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d',
                              'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']

        self.action_space = spaces.Discrete(3)
        self.observation_space = spaces.Box(
            low=-np.inf, high=np.inf, shape=(len(self.state_columns),), dtype=np.float32
        )

        self.reset()

    def reset(self):
        self.current_step = 0
        self.portfolio = {
            'cash': 10_000_000.0,  # $10 million
            'holdings': {}
        }
        self.total_shares_traded = 0
        self.cumulative_reward = 0
        self.trades = []
        return self._next_observation()

    def _next_observation(self):
        return torch.tensor(self.data[self.state_columns].iloc[self.current_step].values, dtype=torch.float32)

    def step(self, action):
        current_price = self.data.iloc[self.current_step]['Close']
        expected_price = self.data.iloc[self.current_step]['ask_px_00']
        actual_price = self.data.iloc[self.current_step]['price']
        transaction_time = self.data.iloc[self.current_step]['ts_in_delta']

        self._take_action(action, current_price)

        reward = 0
        if action != 0:
            transaction_cost = self._calculate_transaction_cost(self.data.iloc[self.current_step]['Volume'], 0.3, self.data['Volume'].mean())
            reward = self._calculate_reward(expected_price, actual_price, transaction_time, transaction_cost)
            self.cumulative_reward += reward
            if self.trades:
                self.trades[-1]['reward'] = reward
                self.trades[-1]['transaction_cost'] = transaction_cost
                self.trades[-1]['slippage'] = expected_price - actual_price
                self.trades[-1]['time_penalty'] = 100 * transaction_time / 1e9

        done = self.current_step == len(self.data) - 1
        obs = self._next_observation()
        info = {
            'step': self.current_step,
            'action': action,
            'price': actual_price,
            'shares': self.trades[-1]['shares'] if self.trades else 0,
            'portfolio_value': self.get_portfolio_value()
        }

        self.current_step += 1
        return obs, reward, done, info

    def _take_action(self, action, current_price):
        current_time = pd.to_datetime(self.data.iloc[self.current_step]['ts_event'])
        symbol = self.data.iloc[self.current_step]['symbol']
        trade_info = {'step': self.current_step, 'timestamp': current_time, 'action': action, 'price': current_price, 'shares': 0, 'reward': 0, 'transaction_cost': 0, 'slippage': 0, 'time_penalty': 0}

        if action == 1:  # Buy
            shares_bought = (self.portfolio['cash'] * np.random.uniform(0.001, 0.005)) // current_price
            cost = shares_bought * current_price
            if self.portfolio['cash'] >= cost:
                self.portfolio['cash'] -= cost
                self.portfolio['holdings'][symbol] = self.portfolio['holdings'].get(symbol, 0) + shares_bought
                self.total_shares_traded += shares_bought
                trade_info['shares'] = shares_bought
                if shares_bought > 0:
                    self.trades.append(trade_info)

        elif action == 2:  # Sell
            shares_held = self.portfolio['holdings'].get(symbol, 0)
            shares_sold = min((self.portfolio['cash'] * np.random.uniform(0.001, 0.005)) // current_price, shares_held)
            if shares_sold > 0:
                self.portfolio['cash'] += shares_sold * current_price
                self.portfolio['holdings'][symbol] -= shares_sold
                self.total_shares_traded += shares_sold
                trade_info['shares'] = shares_sold
                self.trades.append(trade_info)

    def _calculate_reward(self, expected_price, actual_price, transaction_time, transaction_cost):
        slippage = expected_price - actual_price
        time_penalty = 100 * transaction_time / 1e9
        reward = - (slippage + time_penalty + transaction_cost)
        return reward

    def _calculate_transaction_cost(self, volume, volatility, daily_volume):
        return volatility * np.sqrt(volume / daily_volume)

    def get_portfolio_value(self):
        step = min(self.current_step, len(self.data) - 1)
        current_price = self.data.iloc[step]['Close']
        symbol = self.data.iloc[step]['symbol']
        holdings_value = self.portfolio['holdings'].get(symbol, 0) * current_price
        return self.portfolio['cash'] + holdings_value

    def run(self):
        self.reset()
        for _ in range(len(self.data)):
            self.step(0)  # Passing 0 as a placeholder action
        return self.cumulative_reward, self.trades

    def render(self, mode='human', close=False):
        print(f'Step: {self.current_step}')
        print(f'Cash: {self.portfolio["cash"]}')
        print(f'Holdings: {self.portfolio["holdings"]}')
        print(f'Total shares traded: {self.total_shares_traded}')
        print(f'Total portfolio value: {self.get_portfolio_value()}')
        print(f'Cumulative reward: {self.cumulative_reward}')
        self.print_trades()

    def print_trades(self):
        trades_df = pd.DataFrame(self.trades)
        trades_df.to_csv('trades_ppo.csv', index=False)
        for trade in self.trades:
            print(f"Step: {trade['step']}, Timestamp: {trade['timestamp']}, Action: {trade['action']}, Price: {trade['price']}, Shares: {trade['shares']}, Reward: {trade['reward']}, Transaction Cost: {trade['transaction_cost']}, Slippage: {trade['slippage']}, Time Penalty: {trade['time_penalty']}")

### Model

In [20]:
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
from typing import List, Dict
from torch.distributions import Categorical
import pandas as pd
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau

# Create a custom logging class
class GoogleDriveLogger:
    def __init__(self, filename):
        self.terminal = sys.stdout
        self.log_file = open(f'/content/drive/MyDrive/{filename}', 'w')

    def write(self, message):
        self.terminal.write(message)
        self.log_file.write(message)
        self.log_file.flush()  # Ensure the message is written immediately

    def flush(self):
        self.terminal.flush()
        self.log_file.flush()


class TransformerPPOActor(nn.Module):
    def __init__(self, input_dim: int, num_heads: int = 4, num_layers: int = 2, dropout: float = 0.1):
        super().__init__()
        self.input_dim = input_dim
        self.embedding = nn.Sequential(
            nn.Linear(input_dim, 32),
            nn.LayerNorm(32)
        )
        self.positional_encoding = nn.Parameter(torch.randn(1, 1, 32))
        encoder_layer = nn.TransformerEncoderLayer(d_model=32, nhead=num_heads, dropout=dropout, batch_first=True)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=num_layers)
        self.fc = nn.Linear(32, 3)  # 3 actions: Buy, Sell, Hold
        self.to(device)

    def forward(self, x: torch.Tensor) -> torch.Tensor:

        if x.dim() == 1:
            x = x.unsqueeze(0)  # Add batch dimension if it's missing
        if x.dim() == 2:
            x = x.unsqueeze(1)  # Add sequence dimension if it's missing

        x = x.to(device)
        if torch.isnan(x).any():
            print(f"NaN detected BEFORE embedding in actor: {x}")
        x = self.embedding(x)
        if torch.isnan(x).any():
            print(f"NaN detected after embedding in actor: {x}")

        x = x + self.positional_encoding
        if torch.isnan(x).any():
            print(f"NaN detected after positional encoding in actor: {x}")

        x = self.transformer_encoder(x)
        if torch.isnan(x).any():
            print(f"NaN detected after transformer encoder in actor: {x}")

        logits = self.fc(x.mean(dim=1))
        if torch.isnan(logits).any():
            print(f"NaN detected in logits: {logits}")
        return logits

class TransformerPPOCritic(nn.Module):
    def __init__(self, input_dim: int, num_heads: int = 4, num_layers: int = 2, dropout: float = 0.1):
        super().__init__()
        self.input_dim = input_dim
        self.embedding = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.LayerNorm(64)
        )
        self.positional_encoding = nn.Parameter(torch.randn(1, 1, 64))
        encoder_layer = nn.TransformerEncoderLayer(d_model=64, nhead=num_heads, dropout=dropout, batch_first=True)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=num_layers)
        self.fc = nn.Linear(64, 1)  # Output a single value (state value)
        self.to(device)

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        if x.dim() == 1:
            x = x.unsqueeze(0)  # Add batch dimension if it's missing
        if x.dim() == 2:
            x = x.unsqueeze(1)  # Add sequence dimension if it's missing

        x = x.to(device)
        if torch.isnan(x).any():
            print(f"NaN detected BEFORE embedding in critic: {x}")
        x = self.embedding(x)
        if torch.isnan(x).any():
            print(f"NaN detected after embedding in critic: {x}")

        x = x + self.positional_encoding
        if torch.isnan(x).any():
            print(f"NaN detected after positional encoding in critic: {x}")

        x = self.transformer_encoder(x)
        if torch.isnan(x).any():
            print(f"NaN detected after transformer encoder in critic: {x}")

        state_value = self.fc(x.mean(dim=1))
        if torch.isnan(state_value).any():
            print(f"NaN detected in state_value in critic: {state_value}")
        return state_value


class PPOMemory:
    def __init__(self, batch_size):
        self.states = []
        self.actions = []
        self.probs = []
        self.vals = []
        self.rewards = []
        self.dones = []
        self.batch_size = batch_size

    def generate_batches(self):
        n_states = len(self.states)
        batch_start = np.arange(0, n_states, self.batch_size)
        indices = np.arange(n_states, dtype=np.int64)
        np.random.shuffle(indices)
        batches = [indices[i:i+self.batch_size] for i in batch_start]
        return np.array(self.states), \
               np.array(self.actions), \
               np.array(self.probs), \
               np.array(self.vals), \
               np.array(self.rewards), \
               np.array(self.dones), \
               batches

    def store_memory(self, state, action, probs, vals, reward, done):
        self.states.append(state)
        self.actions.append(action)
        self.probs.append(probs)
        self.vals.append(vals)
        self.rewards.append(reward)
        self.dones.append(done)

    def clear_memory(self):
        self.states = []
        self.actions = []
        self.probs = []
        self.vals = []
        self.rewards = []
        self.dones = []

def compute_gae(next_value, rewards, masks, values, gamma=0.99, tau=0.95):
    values = torch.cat([values, next_value.unsqueeze(0)])
    gae = 0
    returns = []
    for step in reversed(range(len(rewards))):
        delta = rewards[step] + gamma * values[step + 1] * masks[step] - values[step]
        gae = delta + gamma * tau * masks[step] * gae
        returns.insert(0, gae + values[step])
    return torch.tensor(returns)

def print_grad_norms(model, model_name):
    for name, param in model.named_parameters():
        if param.grad is not None:
            print(f"{model_name} - Layer: {name}, Grad norm: {param.grad.norm()}")

class EarlyStopping:
    def __init__(self, patience=5, min_delta=0):
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_score = None
        self.early_stop = False

    def __call__(self, score):
        if self.best_score is None:
            self.best_score = score
        elif score < self.best_score + self.min_delta:
            self.counter += 1
            if self.counter >= self.patience:
                self.early_stop = True
        else:
            self.best_score = score
            self.counter = 0

def train_ppo_agent(env, actor, critic, num_episodes, batch_size, n_epochs, alpha, actor_lr, critic_lr, clip_epsilon):
    memory = PPOMemory(batch_size)
    actor_optimizer = optim.Adam(actor.parameters(), lr=actor_lr)
    critic_optimizer = optim.Adam(critic.parameters(), lr=critic_lr)

    # Learning rate schedulers
    actor_scheduler = ReduceLROnPlateau(actor_optimizer, mode='max', factor=0.5, patience=10, verbose=True)
    critic_scheduler = ReduceLROnPlateau(critic_optimizer, mode='min', factor=0.5, patience=10, verbose=True)

    # Early stopping
    early_stopping = EarlyStopping(patience=20, min_delta=0.01)

    best_score = float('-inf')
    scores = []

    for episode in tqdm(range(num_episodes)):
        state = env.reset()
        done = False
        score = 0
        step_count = 0

        while not done and step_count < env.max_steps:
            with torch.no_grad():
                action_logits = actor(state)
                action_probs = F.softmax(action_logits, dim=-1)

            if torch.isnan(action_probs).any():
                print(f"NaN detected in action_probs: {action_probs}")
                action_probs = torch.where(torch.isnan(action_probs), torch.full_like(action_probs, 1e-6), action_probs)
                action_probs = action_probs / action_probs.sum()

            dist = Categorical(action_probs)
            action = dist.sample()
            action_log_prob = dist.log_prob(action)

            with torch.no_grad():
                value = critic(state)

            next_state, reward, done, _ = env.step(action.item())
            score += reward
            step_count += 1

            memory.store_memory(state.cpu().numpy(), action.cpu().numpy(), action_log_prob.cpu().detach().numpy(),
                                value.cpu().detach().numpy(), reward, done)

            if step_count % batch_size == 0:
                print(step_count)
                actor_loss, critic_loss = learn(memory, actor, critic, actor_optimizer, critic_optimizer, n_epochs, clip_epsilon)
                memory.clear_memory()

            state = next_state

        if len(memory.states) > 0:
            actor_loss, critic_loss = learn(memory, actor, critic, actor_optimizer, critic_optimizer, n_epochs, clip_epsilon)
            memory.clear_memory()

        scores.append(score)
        avg_score = np.mean(scores[-100:])  # Moving average of last 100 episodes

        print(f'Episode {episode + 1}, Score: {score:.2f}, Avg Score: {avg_score:.2f}, Steps: {step_count}')

        # Update learning rate schedulers
        actor_scheduler.step(avg_score)
        critic_scheduler.step(critic_loss)

        # Check for early stopping
        early_stopping(avg_score)
        if early_stopping.early_stop:
            print("Early stopping triggered")
            break

        # Save best model
        if avg_score > best_score:
            best_score = avg_score
            torch.save(actor.state_dict(), 'best_actor.pth')
            torch.save(critic.state_dict(), 'best_critic.pth')

    return actor, critic

def learn(memory, actor, critic, actor_optimizer, critic_optimizer, n_epochs, clip_epsilon):
    states, actions, old_probs, vals, rewards, dones, batches = memory.generate_batches()

    states = torch.tensor(states, dtype=torch.float).to(device)
    old_probs = torch.tensor(old_probs).to(device)
    actions = torch.tensor(actions).to(device)

    # Compute GAE
    next_value = critic(states[-1:]).detach()
    values = torch.tensor(vals).to(device)
    rewards = torch.tensor(rewards).to(device)
    masks = torch.tensor(1 - np.array(dones)).to(device)

    returns = compute_gae(next_value, rewards, masks, values)
    returns = returns.to(device)

    total_actor_loss = 0
    total_critic_loss = 0

    for _ in range(n_epochs):
        for batch in batches:
            states_batch = states[batch]
            old_probs_batch = old_probs[batch]
            actions_batch = actions[batch]
            returns_batch = returns[batch]

            new_logits = actor(states_batch)
            new_probs = F.softmax(new_logits, dim=-1)
            critic_value = critic(states_batch).squeeze()

            actions_batch = actions_batch.long().view(-1, 1)
            new_probs_actions = new_probs.gather(1, actions_batch).squeeze()

            old_probs_batch = old_probs_batch.view(-1)

            ratio = new_probs_actions / (old_probs_batch + 1e-8)

            advantage = returns_batch - critic_value.detach()

            surr1 = ratio * advantage
            surr2 = torch.clamp(ratio, 1-clip_epsilon, 1+clip_epsilon) * advantage
            actor_loss = -torch.min(surr1, surr2).mean()

            critic_loss = F.mse_loss(critic_value, returns_batch)

            total_actor_loss += actor_loss.item()
            total_critic_loss += critic_loss.item()

            actor_optimizer.zero_grad()
            actor_loss.backward()
            torch.nn.utils.clip_grad_norm_(actor.parameters(), max_norm=1.0)
            actor_optimizer.step()

            critic_optimizer.zero_grad()
            critic_loss.backward()
            torch.nn.utils.clip_grad_norm_(critic.parameters(), max_norm=1.0)
            critic_optimizer.step()

    return total_actor_loss / (n_epochs * len(batches)), total_critic_loss / (n_epochs * len(batches))




In [21]:
import sys

state_dims = ['Close', 'Volume', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d', 'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']

daily_trading_limit=1000

env = TradingEnvironment(train_df, daily_trading_limit)
input_dim = len(env.state_columns)
actor = TransformerPPOActor(input_dim, num_heads = 4, num_layers = 2, dropout = 0.3)
critic = TransformerPPOCritic(input_dim, num_heads = 4, num_layers = 2, dropout = 0.3)

# Hyperparameters
num_episodes = 3 # 4 runs thru the dataset
batch_size = 128
n_epochs = 2 # 2 run through the batch when doing gradient update
alpha = 0.0003
actor_lr = 0.0001
critic_lr = 0.00005
clip_epsilon = 0.2

train_ppo_agent(env, actor, critic, num_episodes, batch_size, n_epochs, alpha, actor_lr, critic_lr, clip_epsilon)

# At the end of your script, restore the original stdout
# sys.stdout = sys.__stdout__

/usr/local/lib/python3.10/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "
  0%|          | 0/3 [00:00<?, ?it/s]

128
256
384
512
640
768
896
1024
1152
1280
1408
1536
1664
1792
1920
2048
2176
2304
2432
2560
2688
2816
2944
3072
3200
3328
3456
3584
3712
3840
3968
4096
4224
4352
4480
4608
4736
4864
4992
5120
5248
5376
5504
5632
5760
5888
6016
6144
6272
6400
6528
6656
6784
6912
7040
7168
7296
7424
7552
7680
7808
7936
8064
8192
8320
8448
8576
8704
8832
8960
9088
9216
9344
9472
9600
9728
9856
9984
10112
10240
10368
10496
10624
10752
10880
11008
11136
11264
11392
11520
11648
11776
11904
12032
12160
12288
12416
12544
12672
12800
12928
13056
13184
13312
13440
13568
13696
13824
13952
14080
14208
14336
14464
14592
14720
14848
14976
15104
15232
15360
15488
15616
15744
15872
16000
16128
16256
16384
16512
16640
16768
16896
17024
17152
17280
17408
17536
17664
17792
17920
18048
18176
18304
18432
18560
18688
18816
18944
19072
19200
19328
19456
19584
19712
19840
19968
20096
20224
20352
20480
20608
20736
20864
20992
21120
21248
21376
21504
21632
21760
21888
22016
22144
22272
22400
22528
22656
22784
22912
23040
23168

 33%|███▎      | 1/3 [06:11<12:23, 371.64s/it]

Episode 1, Score: -8030.17, Avg Score: -8030.17, Steps: 41464
128
256
384
512
640
768
896
1024
1152
1280
1408
1536
1664
1792
1920
2048
2176
2304
2432
2560
2688
2816
2944
3072
3200
3328
3456
3584
3712
3840
3968
4096
4224
4352
4480
4608
4736
4864
4992
5120
5248
5376
5504
5632
5760
5888
6016
6144
6272
6400
6528
6656
6784
6912
7040
7168
7296
7424
7552
7680
7808
7936
8064
8192
8320
8448
8576
8704
8832
8960
9088
9216
9344
9472
9600
9728
9856
9984
10112
10240
10368
10496
10624
10752
10880
11008
11136
11264
11392
11520
11648
11776
11904
12032
12160
12288
12416
12544
12672
12800
12928
13056
13184
13312
13440
13568
13696
13824
13952
14080
14208
14336
14464
14592
14720
14848
14976
15104
15232
15360
15488
15616
15744
15872
16000
16128
16256
16384
16512
16640
16768
16896
17024
17152
17280
17408
17536
17664
17792
17920
18048
18176
18304
18432
18560
18688
18816
18944
19072
19200
19328
19456
19584
19712
19840
19968
20096
20224
20352
20480
20608
20736
20864
20992
21120
21248
21376
21504
21632
21760
218

 67%|██████▋   | 2/3 [12:24<06:12, 372.24s/it]

Episode 2, Score: -8458.16, Avg Score: -8244.17, Steps: 41464
128
256
384
512
640
768
896
1024
1152
1280
1408
1536
1664
1792
1920
2048
2176
2304
2432
2560
2688
2816
2944
3072
3200
3328
3456
3584
3712
3840
3968
4096
4224
4352
4480
4608
4736
4864
4992
5120
5248
5376
5504
5632
5760
5888
6016
6144
6272
6400
6528
6656
6784
6912
7040
7168
7296
7424
7552
7680
7808
7936
8064
8192
8320
8448
8576
8704
8832
8960
9088
9216
9344
9472
9600
9728
9856
9984
10112
10240
10368
10496
10624
10752
10880
11008
11136
11264
11392
11520
11648
11776
11904
12032
12160
12288
12416
12544
12672
12800
12928
13056
13184
13312
13440
13568
13696
13824
13952
14080
14208
14336
14464
14592
14720
14848
14976
15104
15232
15360
15488
15616
15744
15872
16000
16128
16256
16384
16512
16640
16768
16896
17024
17152
17280
17408
17536
17664
17792
17920
18048
18176
18304
18432
18560
18688
18816
18944
19072
19200
19328
19456
19584
19712
19840
19968
20096
20224
20352
20480
20608
20736
20864
20992
21120
21248
21376
21504
21632
21760
218

100%|██████████| 3/3 [18:36<00:00, 372.02s/it]

Episode 3, Score: -7529.34, Avg Score: -8005.89, Steps: 41464


(TransformerPPOActor(
   (embedding): Sequential(
     (0): Linear(in_features=17, out_features=32, bias=True)
     (1): LayerNorm((32,), eps=1e-05, elementwise_affine=True)
   )
   (transformer_encoder): TransformerEncoder(
     (layers): ModuleList(
       (0-1): 2 x TransformerEncoderLayer(
         (self_attn): MultiheadAttention(
           (out_proj): NonDynamicallyQuantizableLinear(in_features=32, out_features=32, bias=True)
         )
         (linear1): Linear(in_features=32, out_features=2048, bias=True)
         (dropout): Dropout(p=0.3, inplace=False)
         (linear2): Linear(in_features=2048, out_features=32, bias=True)
         (norm1): LayerNorm((32,), eps=1e-05, elementwise_affine=True)
         (norm2): LayerNorm((32,), eps=1e-05, elementwise_affine=True)
         (dropout1): Dropout(p=0.3, inplace=False)
         (dropout2): Dropout(p=0.3, inplace=False)
       )
     )
   )
   (fc): Linear(in_features=32, out_features=3, bias=True)
 ),
 TransformerPPOCritic(
   (em

We are not doing fine-tuning since we are training a Transformer model from scratch.

In [22]:
# run an inference loop:
# calculate performance
observations = []
# Evaluate the model
rewards_list = []
action_probs_list = []

model_inputs = []
recommendations = []
test_env = TradingEnvironment(test_df, daily_trading_limit)
obs = test_env.reset()
for _ in tqdm(range(len(test_df))):
    observations.append(obs)
    # todo - model should learn other features?
    with torch.no_grad():
      action_logits = actor(obs)
      action_probs = F.softmax(action_logits, dim=-1)
    action_probs_list.append(action_probs)

    # prep for example recommendations
    model_inputs.append(obs)
    recommendations.append(action_probs)

    action = torch.argmax(action_probs).item()
    obs, rewards, done, info = test_env.step(action)
    rewards_list.append(rewards)
    if done:
        break

100%|█████████▉| 17770/17771 [01:29<00:00, 197.48it/s]


In [39]:
# example recommendations
len(model_inputs), len(recommendations)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


(17771, 17771)

In [42]:
test_df.index[:3]

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Index([41500, 41501, 41502], dtype='int64')

In [62]:
import torch
import random

def display_trade_recommendations(test_df, state_cols, recommendations, num_examples=3):
    # Create a private copy of test_df and reset its index
    test_df_private = test_df.copy().reset_index(drop=True)

    # Initialize lists to store indices for each action
    hold_indices = []
    buy_indices = []
    sell_indices = []

    # Iterate through recommendations to categorize them
    for idx, recommendation_tensor in enumerate(recommendations):
        recommendation = recommendation_tensor.cpu().numpy().flatten()
        action = torch.argmax(recommendation_tensor).item()

        if action == 0:
            hold_indices.append(idx)
        elif action == 1:
            buy_indices.append(idx)
        elif action == 2:
            sell_indices.append(idx)

    # Randomly sample from the indices
    hold_samples = random.sample(hold_indices, min(num_examples, len(hold_indices)))
    buy_samples = random.sample(buy_indices, min(num_examples, len(buy_indices)))
    sell_samples = random.sample(sell_indices, min(num_examples, len(sell_indices)))

    # Function to display a single trade recommendation
    def display_single_recommendation(index):
        # Extract the input data for the given index
        input_data = test_df_private.loc[index, state_cols]
        recommendation_tensor = recommendations[index]
        recommendation = recommendation_tensor.cpu().numpy().flatten()

        # Get the symbol and the action with the highest probability
        symbol = test_df_private.loc[index, 'symbol'] if 'symbol' in test_df_private.columns else 'Unknown Symbol'
        action = torch.argmax(recommendation_tensor).item()

        # Map action to its meaning
        action_map = {0: "Hold", 1: "Buy", 2: "Sell"}
        action_str = action_map.get(action, "Unknown Action")

        # Calculate percentage likelihoods
        hold_prob = recommendation[0] * 100
        buy_prob = recommendation[1] * 100
        sell_prob = recommendation[2] * 100

        # Print out the trade recommendation details
        print(f"Trade Recommendation for {symbol} at index {index}:")
        print("-" * 50)
        print("Input Data:")
        print(input_data.to_frame().T)
        print("\nRecommendation Probabilities:")
        print(f"Hold: {hold_prob:.2f}%, Buy: {buy_prob:.2f}%, Sell: {sell_prob:.2f}%")
        print(f"\nRecommended Action: {action_str}")
        print("=" * 50)

    # Display examples
    print("\n=== Hold Recommendations ===")
    for idx in hold_samples:
        display_single_recommendation(idx)

    print("\n=== Buy Recommendations ===")
    for idx in buy_samples:
        display_single_recommendation(idx)

    print("\n=== Sell Recommendations ===")
    for idx in sell_samples:
        display_single_recommendation(idx)

# Example usage:
display_trade_recommendations(test_df, state_cols=state_dims, recommendations=recommendations, num_examples=3)



=== Hold Recommendations ===
Trade Recommendation for AAPL at index 2362:
--------------------------------------------------
Input Data:
       Close Volume  RSI      MACD MACD_signal MACD_hist Stoch_k Stoch_d  \
2362  192.28    100  0.0  0.003045    0.005822 -0.002777     0.0     0.0   

           OBV    Upper_BB  Middle_BB    Lower_BB ATR_1       ADX       +DI  \
2362  912052.0  192.298419  192.28725  192.276081  0.01  50.40793  6.955222   

           -DI  CCI  
2362  4.606997  0.0  

Recommendation Probabilities:
Hold: 36.16%, Buy: 28.72%, Sell: 35.12%

Recommended Action: Hold
Trade Recommendation for AAPL at index 5195:
--------------------------------------------------
Input Data:
       Close Volume    RSI      MACD MACD_signal MACD_hist    Stoch_k  \
5195  192.23    100  100.0  0.004312     0.00405  0.000262  88.888889   

        Stoch_d       OBV    Upper_BB Middle_BB    Lower_BB ATR_1        ADX  \
5195  96.296296  915926.0  192.236577  192.2235  192.210423  0.02  30.8508

In [23]:
test_env.render()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Streaming output truncated to the last 5000 lines.
Step: 3042, Timestamp: 2023-07-03 15:42:10.528767677, Action: 1, Price: 192.36, Shares: 19.0, Reward: -0.03722065442150785, Transaction Cost: 0.020331554421507844, Slippage: 0.0, Time Penalty: 0.0168891
Step: 3043, Timestamp: 2023-07-03 15:42:10.538429313, Action: 2, Price: 192.36, Shares: 20.0, Reward: -0.22017414421507842, Transaction Cost: 0.20331554421507841, Slippage: 0.0, Time Penalty: 0.0168586
Step: 3044, Timestamp: 2023-07-03 15:42:10.743799599, Action: 1, Price: 192.37, Shares: 6.0, Reward: -0.15287931332418384, Transaction Cost: 0.13638821332418383, Slippage: 0.0, Time Penalty: 0.0164911
Step: 3045, Timestamp: 2023-07-03 15:42:10.746106080, Action: 2, Price: 192.37, Shares: 24.0, Reward: -0.16727114314108957, Transaction Cost: 0.15078284314108956, Slippage: 0.0, Time Penalty: 0.0164883
Step: 3046, Timestamp: 2023-07-03 15:42:11.024096647, Action: 1, Price: 192.37, Shares: 11.0, Reward: -0.09426523742082375, Transaction Cost:

In [25]:
test_env.cumulative_reward

-3174.2366158455893

In [26]:
row = test_env.data.iloc[test_env.current_step-1]
print(f'Cash {test_env.portfolio["cash"]}, Holdings Value: {test_env.portfolio["holdings"][row["symbol"]]*row["Close"]}')
print(f'Total portfolio value: {test_env.portfolio["cash"] + test_env.portfolio["holdings"][row["symbol"]]*row["Close"]}')

Cash 38446.44500000979, Holdings Value: 9968332.649999999
Total portfolio value: 10006779.095000008


# Baseline #1 - PPO Agent

In [27]:
import pandas as pd
from stable_baselines3 import PPO
from tqdm import tqdm
# Define the daily trading limit (total number of shares to trade per day)
daily_trading_limit = 1000

# ticker = 'AAPL'  # Specify the ticker you want to trade
# ticker_data = market_features_df[market_features_df['symbol'] == ticker]
# ticker = 'AAPL'  # Specify the ticker you want to trade
# Create the trading environment
env = TradingEnvironment(train_df, daily_trading_limit)  # Adjust window_size if needed

# Define the best hyperparameters
best_hyperparameters = {'learning_rate': 0.0009931989008886031,'n_steps': 512,'batch_size': 128, 'gamma': 0.9916829193042708,'clip_range': 0.21127653449387027,'n_epochs': 6} # type: ignore

# Create the RL model with the best hyperparameters
ppo_model = PPO('MlpPolicy', env, verbose=1, **best_hyperparameters)

# Train the model
ppo_model.learn(total_timesteps=10000)

# Save the model
ppo_model.save("trading_agent")

Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.10/dist-packages/stable_baselines3/common/vec_env/patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


----------------------------
| time/              |     |
|    fps             | 174 |
|    iterations      | 1   |
|    time_elapsed    | 2   |
|    total_timesteps | 512 |
----------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 174         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 1024        |
| train/                  |             |
|    approx_kl            | 0.009783706 |
|    clip_fraction        | 0.149       |
|    clip_range           | 0.211       |
|    entropy_loss         | -1.09       |
|    explained_variance   | 0.0609      |
|    learning_rate        | 0.000993    |
|    loss                 | 0.17        |
|    n_updates            | 6           |
|    policy_gradient_loss | -0.0126     |
|    value_loss           | 0.983       |
-----------------------------------------
-----------------------------------------

In [28]:
observations = []
# Evaluate the model
# TODO - eval on the test set (create a new environment with the last 10K trades in the day)
rewards_list = []
observations = []
# Evaluate the model
rewards_list = []
action_probs_list = []

test_env = TradingEnvironment(test_df, daily_trading_limit)
obs = test_env.reset()

for _ in tqdm(range(len(test_df))):
    observations.append(obs)
    action, _states = ppo_model.predict(obs)
    obs, rewards, done, info = test_env.step(action)
    rewards_list.append(rewards)
    if done:
        break

# Render the final state
test_env.render()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
100%|█████████▉| 17770/17771 [01:13<00:00, 242.80it/s]


Streaming output truncated to the last 5000 lines.
Step: 9816, Timestamp: 2023-07-03 16:40:49.858701506, Action: 2, Price: 192.17, Shares: 208.0, Reward: -0.19405338217690044, Transaction Cost: 0.17724638217690045, Slippage: 0.0, Time Penalty: 0.016807
Step: 9817, Timestamp: 2023-07-03 16:40:49.858733447, Action: 2, Price: 192.17, Shares: 78.0, Reward: -0.11641706802064285, Transaction Cost: 0.09960386802064285, Slippage: 0.0, Time Penalty: 0.0168132
Step: 9819, Timestamp: 2023-07-03 16:40:49.858733447, Action: 2, Price: 192.17, Shares: 167.0, Reward: -0.10064234641287059, Transaction Cost: 0.08382914641287059, Slippage: 0.0, Time Penalty: 0.0168132
Step: 9820, Timestamp: 2023-07-03 16:40:49.858733447, Action: 2, Price: 192.17, Shares: 176.0, Reward: -0.1121766432803481, Transaction Cost: 0.0953634432803481, Slippage: 0.0, Time Penalty: 0.0168132
Step: 9821, Timestamp: 2023-07-03 16:40:49.860158257, Action: 1, Price: 192.17, Shares: 133.0, Reward: -0.22980394421509776, Transaction Cost

In [29]:
test_env.cumulative_reward

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


-2651.4278785403512

In [30]:
row = test_env.data.iloc[test_env.current_step-1]
print(f'Cash {test_env.portfolio["cash"]}, Holdings Value: {test_env.portfolio["holdings"][row["symbol"]]*row["Close"]}')
print(f'Total portfolio value: {test_env.portfolio["cash"] + test_env.portfolio["holdings"][row["symbol"]]*row["Close"]}')

Cash 10000321.125000037, Holdings Value: 0.0
Total portfolio value: 10000321.125000037


# Baseline # 2 - Simple Mean Reversion Bot

In [31]:
import pandas as pd
import numpy as np
from scipy.stats import norm
import matplotlib.pyplot as plt

INITIAL_CASH = 10_000_000  # $10 million

def preprocess_data(df):
    df['liquidity'] = df['bid_sz_00'] * df['bid_px_00'] + df['ask_sz_00'] * df['ask_px_00']
    return df

def calculate_rsi(data, window=14):
    delta = data.diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=window).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=window).mean()
    rs = gain / loss
    rsi = 100 - (100 / (1 + rs))
    return rsi

def calculate_vol_and_liquidity(price_df, volume_df, window_size):
    # Calculate rolling statistics
    rolling_mean_vol = price_df.pct_change().rolling(window=window_size).mean()
    rolling_std_vol = price_df.pct_change().rolling(window=window_size).std()
    rolling_mean_liq = volume_df.rolling(window=window_size).mean()
    rolling_std_liq = volume_df.rolling(window=window_size).std()

    return rolling_mean_vol, rolling_std_vol, rolling_mean_liq, rolling_std_liq

def get_percentile(current_value, mean, std):
    if std > 0:
        z_score = (current_value - mean) / std
        percentile = norm.cdf(z_score)
    else:
        percentile = 0.5  # No variation
    return percentile

def get_trade_price(base_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction):
    vol_percentile = get_percentile(current_vol, mean_vol, std_vol)
    liq_percentile = get_percentile(current_liq, mean_liq, std_liq)

    # Define price adjustment scenarios based on market conditions
    if vol_percentile >= 0.9 and liq_percentile < 0.1:
        price_adjustment_percent = np.random.uniform(-0.25, -0.15)
    elif vol_percentile <= 0.1 and liq_percentile < 0.1:
        price_adjustment_percent = np.random.uniform(-0.10, -0.05)
    elif vol_percentile >= 0.9 and liq_percentile >= 0.9:
        price_adjustment_percent = np.random.uniform(-0.05, +0.10)
    else:
        price_adjustment_percent = np.random.uniform(-0.05, +0.05)  # Default for normal conditions

    # Adjust price based on trade direction
    if trade_direction == 'BUY':
        adjusted_price = base_price * (1 - price_adjustment_percent)
    else:  # SELL
        adjusted_price = base_price * (1 + price_adjustment_percent)

    return adjusted_price


class TradingEnvironmentwithBlotter:
    def __init__(self, data, daily_trading_limit, window_size):
        self.data = preprocess_data(data)
        self.daily_trading_limit = daily_trading_limit
        self.window_size = window_size
        self.state_columns = ['price', 'liquidity', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d',
                              'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']
        self.reset()

    def reset(self):
        self.current_step = 0
        self.balance = INITIAL_CASH
        self.shares_held = 0
        self.total_shares_traded = 0
        self.cumulative_reward = 0
        self.trades = []
        self.portfolio = {'cash': self.balance, 'holdings': {ticker: 0 for ticker in self.data['symbol'].unique()}}
        self.data['RSI'] = calculate_rsi(self.data['price'])
        self.data['pct_change'] = self.data['price'].pct_change()
        self.data['rolling_mean_vol'], self.data['rolling_std_vol'], self.data['rolling_mean_liq'], self.data['rolling_std_liq'] = calculate_vol_and_liquidity(self.data['price'], self.data['liquidity'], self.window_size)

    def step(self):
        row = self.data.iloc[self.current_step]
        current_price = row['price']
        current_time = pd.to_datetime(row['ts_event'])
        current_rsi = row['RSI']
        current_vol = row['pct_change']
        current_liq = row['liquidity']
        mean_vol = row['rolling_mean_vol']
        std_vol = row['rolling_std_vol']
        mean_liq = row['rolling_mean_liq']
        std_liq = row['rolling_std_liq']

        if current_rsi < 30:  # Entry signal based on RSI
            trade_direction = 'BUY'
            trade_price = get_trade_price(current_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction)
            trade_size = (self.portfolio['cash'] * np.random.uniform(0.001, 0.005)) / trade_price
            if self.portfolio['cash'] >= trade_size * trade_price:
                self.portfolio['cash'] -= trade_size * trade_price
                self.portfolio['holdings'][row['symbol']] += trade_size
                trade_status = 'filled'
            else:
                trade_status = 'cancelled'
        elif current_rsi > 70:  # Exit signal based on RSI
            trade_direction = 'SELL'
            if self.portfolio['holdings'][row['symbol']] > 0:
                trade_size = min(self.portfolio['holdings'][row['symbol']], self.portfolio['cash']*np.random.uniform(0.001, 0.005) / current_price)
                trade_price = get_trade_price(current_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction)
                self.portfolio['cash'] += trade_size * trade_price
                self.portfolio['holdings'][row['symbol']] -= trade_size
                trade_status = 'filled'
            else:
                trade_size = 0
                trade_status = 'cancelled'
        else:
            trade_direction = 'HOLD'
            trade_size = 0
            trade_price = current_price
            trade_status = 'skipped'

        if trade_size > 0:
            expected_price = row['ask_px_00']
            actual_price = row['price']
            transaction_time = row['ts_in_delta']
            transaction_cost = self._calculate_transaction_cost(row['Volume'], 0.3, self.data['Volume'].mean())
            slippage = expected_price - actual_price
            time_penalty = 1000 * transaction_time / 1e9
            reward = - (slippage + time_penalty + transaction_cost)

            self.cumulative_reward += reward
            self.trades.append({
                'step': self.current_step,
                'timestamp': current_time,
                'action': trade_direction,
                'price': trade_price,
                'shares': trade_size,
                'symbol': row['symbol'],
                'reward': reward,
                'transaction_cost': transaction_cost,
                'slippage': slippage,
                'time_penalty': time_penalty
            })



        self.current_step += 1
        if self.current_step >= len(self.data) - 1:
            done=True
            self.current_step = 0

    def _calculate_transaction_cost(self, volume, volatility, daily_volume):
        return volatility * np.sqrt(volume / daily_volume)

    def run(self):
        self.reset()
        for _ in range(len(self.data)):
            self.step()
        return self.cumulative_reward, self.trades

    def render(self):
        print(f'Cumulative reward: {self.cumulative_reward}')
        row = self.data.iloc[self.current_step]
        print(f'Total portfolio value: {self.portfolio["cash"] + self.portfolio["holdings"][row["symbol"]]*row["Close"]}')
        # get trades in a pandas dataframe
        trades_df = pd.DataFrame(self.trades)
        # Save a csv
        trades_df.to_csv('trades_blotter.csv', index=False)
        for trade in self.trades:
            print(f"Step: {trade['step']}, Timestamp: {trade['timestamp']}, Action: {trade['action']}, Price: {trade['price']}, Shares: {trade['shares']}, Symbol: {trade['symbol']}, Reward: {trade['reward']}, Transaction Cost: {trade['transaction_cost']}, Slippage: {trade['slippage']}, Time Penalty: {trade['time_penalty']}")

In [32]:
# Filter data for the specified ticker

window_size = 60
daily_trading_limit = 1000
# Create the trading environment
env = TradingEnvironmentwithBlotter(test_df, daily_trading_limit=1000, window_size=window_size)  # Daily trading limit of 1000 shares

# Run the environment
cumulative_reward, trades = env.run()

# Render the results
env.render()

Streaming output truncated to the last 5000 lines.
Step: 8350, Timestamp: 2023-07-03 16:29:54.454344746, Action: SELL, Price: 192.89470407254936, Shares: 50.51272654195409, Symbol: AAPL, Reward: -0.23509202034363189, Transaction Cost: 0.06429402034363188, Slippage: 0.0, Time Penalty: 0.170798
Step: 8351, Timestamp: 2023-07-03 16:29:54.454344746, Action: SELL, Price: 193.38355883010703, Shares: 22.53336383465464, Symbol: AAPL, Reward: -0.19112955442150786, Transaction Cost: 0.020331554421507844, Slippage: 0.0, Time Penalty: 0.170798
Step: 8352, Timestamp: 2023-07-03 16:29:54.454344746, Action: SELL, Price: 184.1558658564314, Shares: 15.394786367643453, Symbol: AAPL, Reward: -0.3741135442150784, Transaction Cost: 0.20331554421507841, Slippage: 0.0, Time Penalty: 0.170798
Step: 8353, Timestamp: 2023-07-03 16:29:54.474421200, Action: SELL, Price: 186.30871945127862, Shares: 24.542669158699155, Symbol: AAPL, Reward: -0.38060254421506934, Transaction Cost: 0.20331554421507841, Slippage: 0.00

In [33]:
cumulative_reward

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


-3392.4109740146782

In [34]:
row = env.data.iloc[env.current_step]
print(f'Cash {env.portfolio["cash"]}, Holdings Value: {env.portfolio["holdings"][row["symbol"]]*row["Close"]}')
print(f'Total portfolio value: {env.portfolio["cash"] + env.portfolio["holdings"][row["symbol"]]*row["Close"]}')

Cash 2972982.9097982734, Holdings Value: 6968943.885627945
Total portfolio value: 9941926.795426218


#3 Simple Momentum Trading Strategy

In [35]:
class MomentumTradingEnvironment:
    def __init__(self, data, lookback_period=20, holding_period=5):
        self.data = data
        self.lookback_period = lookback_period
        self.holding_period = holding_period
        self.reset()

    def reset(self):
        self.current_step = self.lookback_period
        self.balance = INITIAL_CASH
        self.portfolio = {'cash': self.balance, 'holdings': {}}
        for symbol in self.data['symbol'].unique():
            self.portfolio['holdings'][symbol] = 0
        self.trades = []
        self.data['returns'] = self.data['Close'].pct_change()
        self.data['momentum'] = self.data['returns'].rolling(window=self.lookback_period).mean()
        self.purchase_times = {symbol: None for symbol in self.data['symbol'].unique()}

    def calculate_portfolio_value(self):
        total_value = self.portfolio['cash']
        for symbol, shares in self.portfolio['holdings'].items():
            current_price = self.data[self.data['symbol'] == symbol].iloc[self.current_step]['Close']
            total_value += shares * current_price
        return total_value

    def step(self):
        if self.current_step >= len(self.data) - 1:
            return True  # Done

        row = self.data.iloc[self.current_step]
        current_price = row['Close']
        momentum = row['momentum']
        symbol = row['symbol']

        # Trading logic
        if self.portfolio['holdings'][symbol] == 0:
            if momentum > 0:  # Positive momentum
                shares_to_buy = self.portfolio['cash'] // current_price
                cost = shares_to_buy * current_price
                if self.portfolio['cash'] >= cost:
                    self.portfolio['cash'] -= cost
                    self.portfolio['holdings'][symbol] += shares_to_buy
                    self.purchase_times[symbol] = self.current_step
                    self.trades.append({
                        'timestamp': self.data.index[self.current_step],
                        'action': 'BUY',
                        'price': current_price,
                        'shares': shares_to_buy,
                        'symbol': symbol
                    })
        elif (self.portfolio['holdings'][symbol] > 0 and
              self.purchase_times[symbol] is not None and
              (self.current_step - self.purchase_times[symbol] >= self.holding_period)):
            # Sell after holding period
            shares_to_sell = self.portfolio['holdings'][symbol]
            sale_proceeds = shares_to_sell * current_price
            self.portfolio['cash'] += sale_proceeds
            self.portfolio['holdings'][symbol] = 0
            self.purchase_times[symbol] = None
            self.trades.append({
                'timestamp': self.data.index[self.current_step],
                'action': 'SELL',
                'price': current_price,
                'shares': shares_to_sell,
                'symbol': symbol
            })

        # Calculate portfolio value after the trade
        portfolio_value = self.calculate_portfolio_value()
        if self.trades:
            self.trades[-1]['portfolio_value'] = portfolio_value

        self.current_step += 1
        return False  # Not done

    def run(self):
        done = False
        step_counter = 0
        while not done:
            done = self.step()
            step_counter += 1
            print(f"\rStep {step_counter}/{len(self.data)} completed", end="", flush=True)
        return self.calculate_portfolio_value(), self.trades

    def render(self):
        for trade in self.trades:
            print(f"Timestamp: {trade['timestamp']}, Action: {trade['action']}, Symbol: {trade['symbol']}, "
                  f"Price: {trade['price']}, Shares: {trade['shares']}, Portfolio Value: {trade['portfolio_value']}")
        print(f"Final Portfolio Value: {self.calculate_portfolio_value()}")

In [36]:
# Filter data for the specified ticker

window_size = 60
daily_trading_limit = 1000
# Create the trading environment
env = MomentumTradingEnvironment(test_df, lookback_period=20, holding_period=5)  # Daily trading limit of 1000 shares

# Run the environment
cumulative_reward, trades = env.run()

# Render the results
env.render()

Step 17751/17771 completedTimestamp: 41549, Action: BUY, Symbol: AAPL, Price: 192.27, Shares: 52010.0, Portfolio Value: 10001040.2
Timestamp: 41554, Action: SELL, Symbol: AAPL, Price: 192.3, Shares: 52010.0, Portfolio Value: 10001560.299999999
Timestamp: 41555, Action: BUY, Symbol: AAPL, Price: 192.3, Shares: 52010.0, Portfolio Value: 10001300.249999998
Timestamp: 41560, Action: SELL, Symbol: AAPL, Price: 192.295, Shares: 52010.0, Portfolio Value: 10001300.249999998
Timestamp: 41561, Action: BUY, Symbol: AAPL, Price: 192.295, Shares: 52010.0, Portfolio Value: 10001040.2
Timestamp: 41566, Action: SELL, Symbol: AAPL, Price: 192.29, Shares: 52010.0, Portfolio Value: 10001040.2
Timestamp: 41567, Action: BUY, Symbol: AAPL, Price: 192.29, Shares: 52010.0, Portfolio Value: 10001040.2
Timestamp: 41572, Action: SELL, Symbol: AAPL, Price: 192.3, Shares: 52010.0, Portfolio Value: 10001560.299999999
Timestamp: 41573, Action: BUY, Symbol: AAPL, Price: 192.3, Shares: 52010.0, Portfolio Value: 100010

In [37]:
cumulative_reward

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


10049549.64

In [38]:
row = env.data.iloc[env.current_step]
print(f'Cash {env.portfolio["cash"]}, Holdings Value: {env.portfolio["holdings"][row["symbol"]]*row["Close"]}')
print(f'Total portfolio value: {env.portfolio["cash"] + env.portfolio["holdings"][row["symbol"]]*row["Close"]}')

Cash 3.0900000017136335, Holdings Value: 10049546.549999999
Total portfolio value: 10049549.64


# Evaluation

See the report.